In [1]:
import pandas as pd
import numpy as np
import warnings 
warnings.filterwarnings('ignore')
import re
from string import punctuation
import seaborn as sns
pd.set_option('display.max_colwidth', -1)
from nltk.corpus import stopwords
import nltk
import gensim 
from gensim.models import Word2Vec
import emoji
from string import punctuation
from imblearn.over_sampling import SMOTE,ADASYN
from nltk.stem.porter import *
from sklearn.model_selection import GridSearchCV
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.preprocessing import MinMaxScaler
from sklearn.naive_bayes import MultinomialNB
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score,precision_score,classification_report,f1_score
from vaderSentiment.vaderSentiment import SentimentIntensityAnalyzer

In [2]:
df = pd.read_csv('train.csv')

In [3]:
df.head()

tweet_id  \
0  1701       
1  1851       
2  2689       
3  4525       
4  3604       

                                                                                                                                             tweet  \
0  #sxswnui #sxsw #apple defining language of touch with different dialects becoming smaller                                                         
1  Learning ab Google doodles! All doodles should be light, funny &amp; innovative, with exceptions for significant occasions. #GoogleDoodle #sxsw   
2  one of the most in-your-face ex. of stealing the show in yrs RT @mention &quot;At #SXSW, Apple schools the mkt experts&quot;  {link}              
3  This iPhone #SXSW app would b pretty awesome if it didn't crash every 10mins during extended browsing. #Fuckit #Illmakeitwork                     
4  Line outside the Apple store in Austin waiting for the new iPad #SXSW  {link}                                                                     

   sentiment  
0  1          
1  1          
2  2          
3  0          
4  1

In [4]:
df_test = pd.read_csv('test.csv')

In [5]:
df_test.head()

tweet_id  \
0  7506       
1  7992       
2  247        
3  7688       
4  3294       

                                                                                                                                        tweet  
0  Audience Q: What prototyping tools do you use? Sketchbooks/sharpie pens, photoshop, Balsamic, Google docs, Axsure, etc. #myprototype #sxsw  
1  At SXSW? Send Your Best Photos &amp; Videos to... {link} #citizen_journalism #cnn #ireport #photography #sxsw #Cyber #iPhone                
2  @mention  and here's a pic of you winning your ipad! #unsix #sxsw cc @mention @mention  {link} (cont) {link}                                
3  Google Marissa Mayer: mobile phone as a cursor of physical location - new version of map fast and more real life like   #sxsw               
4  #SXSW Google maps is even cooler than I thought

In [6]:
df.isnull().sum()

tweet_id     0
tweet        1
sentiment    0
dtype: int64

In [7]:
df_test.isnull().sum()

tweet_id    0
tweet       0
dtype: int64

In [8]:
df = df.fillna('Aplle is good')

In [9]:
df.isnull().sum()

tweet_id     0
tweet        0
sentiment    0
dtype: int64

In [ ]:
# analyser = SentimentIntensityAnalyzer()
# vs_polarity = []

# for sentence in df['tweet']:
#     vs_polarity.append(analyser.polarity_scores(sentence)['compound'])

In [165]:
# analyser = SentimentIntensityAnalyzer()
# vs_polarity = []

# for sentence in df_test['tweet']:
#     vs_polarity.append(analyser.polarity_scores(sentence)['compound'])

In [166]:
# pd.DataFrame(vs_polarity).to_csv('polarity_hack_test.csv')

In [167]:
# word_count = []
# for i in df['tweet']:
#     word_count.append(len(nltk.word_tokenize(i)))

In [ ]:
# word_count = []
# for i in df_test['tweet']:
#     word_count.append(len(nltk.word_tokenize(i)))

In [169]:
# pd.DataFrame(word_count).to_csv('word_count_hack_test.csv')

In [170]:
# def extracting_emoticons(df,col,emo_list):
#     m= 0
#     n=1
#     for j in range(len(df)):
#         for i in emo_list:
#             if i in str(df[col][m:n]):
#                 if i in df.columns:
#                     df[i][m:n] = 1 
#                 else:
#                     df[i] = np.zeros(len(df),dtype='int8')
#                     df[i][m:n] = 1
#         m+=1
#         n+=1
# emo_list = [':)', ';-)',
#        ':-)', ':(', ':P', ';)', ':-(',
#        ':D', ':-|', ':-/', ':p', '=)', ';]', 'xD', ':]',
#        ':-D', '=D', ':O']

In [21]:
# extracting_emoticons(df,'tweet',emo_list)

In [22]:
# df.head()

tweet_id  \
0  1701       
1  1851       
2  2689       
3  4525       
4  3604       

                                                                                                                                             tweet  \
0  #sxswnui #sxsw #apple defining language of touch with different dialects becoming smaller                                                         
1  Learning ab Google doodles! All doodles should be light, funny &amp; innovative, with exceptions for significant occasions. #GoogleDoodle #sxsw   
2  one of the most in-your-face ex. of stealing the show in yrs RT @mention &quot;At #SXSW, Apple schools the mkt experts&quot;  {link}              
3  This iPhone #SXSW app would b pretty awesome if it didn't crash every 10mins during extended browsing. #Fuckit #Illmakeitwork                     
4  Line outside the Apple store in Austin waiting for the new iPad #SXSW  {link}                                                                     

   sentiment  :)  ;-)  :-)  :(  :P  ;)  :-( ...  :-|  :-/  :p  =)  ;]  xD  :]  \
0  1          0   0    0    0   0   0   0   ...  0    0    0   0   0   0   0    
1  1          0   0    0    0   0   0   0   ...  0    0    0   0   0   0   0    
2  2          0   0    0    0   0   0   0   ...  0    0    0   0   0   0   0    
3  0          0   0    0    0   0   0   0   ...  0    0    0   0   0   0   0    
4  1          0   0    0    0   0   0   0   ...  0    0    0   0   0   0   0    

   :-D  =D  :O  
0  0    0   0   
1  0    0   0   
2  0    0   0   
3  0    0   0   
4  0    0   0   

[5 rows x 21 columns]

In [23]:
# df['tweet'][df[':(']== 1]

535     I won an iPad at #SXSW! Nah I'm lying, I bought this shit myself :( {link}                                                                       
657     shoot, my ipad will not display any search results :( will have to go through questions later #osmpw #sxsw                                       
845     @mention I would have been a #SXSW ambassador since I'm going to be everywhere but you only have iphone &amp; Android listed for mobile. :(      
924     Will I be the only one at #sxsw with a blackberry, a dell &amp; no iPad? Feeling like a dork @mention a geek conference. Does that make sense? :(
1802    SHITE APP. :( RT @mention New #UberSocial for #iPhone now in the App Store includes UberGuide to #SXSW sponsoÛ_ (cont) {link}                   
1949    Grrrr @mention not muting #sxsw as thought on web or iphone :(                                                                                   
3527    this is not how I want 2 B spending my  time during #sxsw :( (@menti

In [171]:
# extracting_emoticons(df_test,'tweet',emo_list)

In [172]:
# df_test.head()

tweet_id  \
0  7506       
1  7992       
2  247        
3  7688       
4  3294       

                                                                                                                                        tweet  \
0  Audience Q: What prototyping tools do you use? Sketchbooks/sharpie pens, photoshop, Balsamic, Google docs, Axsure, etc. #myprototype #sxsw   
1  At SXSW? Send Your Best Photos &amp; Videos to... {link} #citizen_journalism #cnn #ireport #photography #sxsw #Cyber #iPhone                 
2  @mention  and here's a pic of you winning your ipad! #unsix #sxsw cc @mention @mention  {link} (cont) {link}                                 
3  Google Marissa Mayer: mobile phone as a cursor of physical location - new version of map fast and more real life like   #sxsw                
4  #SXSW Google maps is even cooler than I thought                                                                                              

   :)  =)  :-D  :-)  ;)  :D  :(  ;-)  :P  =D  :p  
0  0   0   0    0    0   0   0   0    0   0   0   
1  0   0   0    0    0   0   0   0    0   0   0   
2  0   0   0    0    0   0   0   0    0   0   0   
3  0   0   0    0    0   0   0   0    0   0   0   
4  0   0   0    0    0   0   0   0    0   0   0

In [173]:
# df_test['tweet'][df_test[':(']== 1]

409     Heartbreaker #Sxsw #apple #ipad2 RT @mention @mention just asked. Sadly no :(                                                  
887     Serious iPad envy. Toting around one's Macbook Pro + cord will do that to a girl. #sxsw :(                                     
1658    Ahhh, darn :( RT @mention @mention @mention according to @mention Google has confirmed it is not launching at #SXSW, if at all.
Name: tweet, dtype: object

In [175]:
# df_test.iloc[:,3:].to_csv(r'emo_hack_test.csv')

In [176]:
# cap_list = ['LAME',
#  'TOP STORY',
#  'APPLAUDS',
#  'HELP ME',
#  'OOPS',
#  'YES',
#  'LOST',
#  'PLEASE RT',
#  'SHITE APP',
#  'SCIENTIFIC DICTATORSHIP',
#  'BEST',
#  'OOOO',
#  'COOL',
#  'WINNING',
#  'KILLING',
#  'AMAZING',
#  'APROVEITEM',
#  'OH SNAP',
#  'WHAT',
#  'IMPORTANT',
#  'BEAUTIFUL',
#  'HELP',
#  'YAY',
#  'VERY BAD',
#  'LIVESTRONG',
#  'A SHOTGUN',
#  'NYC',
#  'SUCKS',
#  'YES PLEASE',
#  'BOOM',
#  'NICE'
#  'FREE',
#  'ALL FREE',
#  'HOORAY RT',
#  'VERY IMPORTANT',
#  'TOAST',
#  'OMG SIGN',
#  'OMG',
#  'I REALLY',
#  'FAIL',
#  'AGREED',
#  'CHAOS',
#  'GREAT',
#  'COME ON',
#  'VERY',
#  'HOOOOOOO',
#  'DOUCHE CAKE',
#  'AWESOME',
#  'EVER',
#  'I KNEW',
#  'WOW',
#  'THANK YOU',
#  'HARD',
#  'TOO MUCH',
#  'KIIIIIILLING',
#  'REALLY',
#  'LOL',
#  'HUGE',
#  'GORGEOUS',
#  'DELICIOUSLY IRONIC',
#  'THE BIG',
#  'GOOD',
#  'SO COOL',]

In [177]:
# def extracting_all_capital(df,col,cap_list):
#     m= 0
#     n=1
#     for j in range(len(df)):
#         for i in cap_list:
#             if i in str(df[col][m:n]):
#                 if i in df.columns:
#                     df[i][m:n] = 1 
#                 else:
#                     df[i] = np.zeros(len(df),dtype='int8')
#                     df[i][m:n] = 1
#         m+=1
#         n+=1
    

In [27]:
# extracting_all_capital(df,'tweet',cap_list)

In [28]:
# df.head()

tweet_id  \
0  1701       
1  1851       
2  2689       
3  4525       
4  3604       

                                                                                                                                             tweet  \
0  #sxswnui #sxsw #apple defining language of touch with different dialects becoming smaller                                                         
1  Learning ab Google doodles! All doodles should be light, funny &amp; innovative, with exceptions for significant occasions. #GoogleDoodle #sxsw   
2  one of the most in-your-face ex. of stealing the show in yrs RT @mention &quot;At #SXSW, Apple schools the mkt experts&quot;  {link}              
3  This iPhone #SXSW app would b pretty awesome if it didn't crash every 10mins during extended browsing. #Fuckit #Illmakeitwork                     
4  Line outside the Apple store in Austin waiting for the new iPad #SXSW  {link}                                                                     

   sentiment  :)  ;-)  :-)  :(  :P  ;)  :-(    ...     LIVESTRONG  ALL FREE  \
0  1          0   0    0    0   0   0   0      ...     0           0          
1  1          0   0    0    0   0   0   0      ...     0           0          
2  2          0   0    0    0   0   0   0      ...     0           0          
3  0          0   0    0    0   0   0   0      ...     0           0          
4  1          0   0    0    0   0   0   0      ...     0           0          

   HOOOOOOO  THANK YOU  SO COOL  TOO MUCH  HARD  OMG SIGN  TOAST  I REALLY  
0  0         0          0        0         0     0         0      0         
1  0         0          0        0         0     0         0      0         
2  0         0          0        0         0     0         0      0         
3  0         0          0        0         0     0         0      0         
4  0         0          0        0         0     0         0      0         

[5 rows x 82 columns]

In [ ]:
# extracting_all_capital(df_test,'tweet',cap_list)

In [179]:
# df_test.head()

tweet_id  \
0  7506       
1  7992       
2  247        
3  7688       
4  3294       

                                                                                                                                        tweet  \
0  Audience Q: What prototyping tools do you use? Sketchbooks/sharpie pens, photoshop, Balsamic, Google docs, Axsure, etc. #myprototype #sxsw   
1  At SXSW? Send Your Best Photos &amp; Videos to... {link} #citizen_journalism #cnn #ireport #photography #sxsw #Cyber #iPhone                 
2  @mention  and here's a pic of you winning your ipad! #unsix #sxsw cc @mention @mention  {link} (cont) {link}                                 
3  Google Marissa Mayer: mobile phone as a cursor of physical location - new version of map fast and more real life like   #sxsw                
4  #SXSW Google maps is even cooler than I thought                                                                                              

   :)  =)  :-D  :-)  ;)  :D  :(  ;-)   ...     YES  OMG  HUGE  VERY  HARD  \
0  0   0   0    0    0   0   0   0     ...     0    0    0     0     0      
1  0   0   0    0    0   0   0   0     ...     0    0    0     0     0      
2  0   0   0    0    0   0   0   0     ...     0    0    0     0     0      
3  0   0   0    0    0   0   0   0     ...     0    0    0     0     0      
4  0   0   0    0    0   0   0   0     ...     0    0    0     0     0      

   GOOD  KIIIIIILLING  NYC  WINNING  AWESOME  
0  0     0             0    0        0        
1  0     0             0    0        0        
2  0     0             0    0        0        
3  0     0             0    0        0        
4  0     0             0    0        0        

[5 rows x 29 columns]

In [185]:
# df_test.iloc[:,13:].to_csv(r'cap_hack_test.csv')

In [30]:
# lowered = df['tweet'].apply(lambda x:x.lower())
# tokens = lowered.apply(lambda x:nltk.word_tokenize(x))
# tags = tokens.apply(lambda x:nltk.pos_tag(x))

In [31]:
# from collections import Counter
# counts = tags.apply(lambda x: Counter(tag for word,tag in x))


In [32]:
# pos_cols = pd.DataFrame(dict(counts[0],index=[0])).set_index('index')
# pos_cols

#  JJ  NN  VBG  IN  NNS  JJR
index                              
0      3  4   2   2    2   1    1

In [33]:
# pos_cols.append(pd.DataFrame(dict(counts[1],index=[1])).set_index('index'))

#    ,    .    :   CC   DT  IN  JJ  JJR   MD  NN  NNS   VB  VBG
index                                                                 
0      3 NaN  NaN  NaN  NaN  NaN   2   4   1.0 NaN   2   1   NaN   2  
1      2  2.0  2.0  1.0  1.0  1.0  2   6  NaN   1.0  3   4    1.0  1

In [34]:
# for i in range(1,len(df)):
#     pos_cols = pos_cols.append(pd.DataFrame(dict(counts[i],index=[i])).set_index('index'))

In [35]:
# pos_cols.head()

#   $  ''    (    )    ,    .    :   CC   CD ...   VB  VBD  VBG  VBN  \
index                                                 ...                       
0      3.0 NaN NaN NaN  NaN  NaN  NaN  NaN  NaN  NaN  ... NaN  NaN   2.0 NaN    
1      2.0 NaN NaN NaN  NaN   2.0  2.0  1.0  1.0 NaN  ...  1.0 NaN   1.0 NaN    
2      1.0 NaN NaN  1.0  1.0  1.0  1.0  2.0  2.0  1.0 ... NaN  NaN   1.0 NaN    
3      3.0 NaN NaN NaN  NaN  NaN   1.0 NaN  NaN   1.0 ...  2.0  1.0 NaN   1.0   
4      1.0 NaN NaN  1.0  1.0 NaN  NaN  NaN  NaN  NaN  ... NaN  NaN   1.0 NaN    

       VBP  VBZ  WDT  WP  WRB  ``  
index                              
0     NaN  NaN  NaN  NaN NaN  NaN  
1     NaN  NaN  NaN  NaN NaN  NaN  
2     NaN  NaN  NaN  NaN NaN  NaN  
3     NaN  NaN  NaN  NaN NaN  NaN  
4     NaN  NaN  NaN  NaN NaN  NaN  

[5 rows x 44 columns]

In [36]:
# pos_cols.fillna(0,inplace=True)

In [37]:
# for cols in pos_cols.columns:
#     pos_cols[cols] = pos_cols[cols].astype('int')

In [38]:
# pos_cols.iloc[:,8:].head()

CC  CD  DT  EX  FW  IN  JJ  JJR  JJS  LS ...  VB  VBD  VBG  VBN  VBP  \
index                                           ...                           
0      0   0   0   0   0   2   4   1    0    0  ...  0   0    2    0    0     
1      1   0   1   0   0   2   6   0    0    0  ...  1   0    1    0    0     
2      2   1   3   0   0   4   2   0    0    0  ...  0   0    1    0    0     
3      0   1   2   0   0   2   3   0    0    0  ...  2   1    0    1    0     
4      0   0   2   0   0   3   3   0    0    0  ...  0   0    1    0    0     

       VBZ  WDT  WP  WRB  ``  
index                         
0      0    0    0   0    0   
1      0    0    0   0    0   
2      0    0    0   0    0   
3      0    0    0   0    0   
4      0    0    0   0    0   

[5 rows x 36 columns]

In [39]:
# df['tweet'].head()

0    #sxswnui #sxsw #apple defining language of touch with different dialects becoming smaller                                                      
1    Learning ab Google doodles! All doodles should be light, funny &amp; innovative, with exceptions for significant occasions. #GoogleDoodle #sxsw
2    one of the most in-your-face ex. of stealing the show in yrs RT @mention &quot;At #SXSW, Apple schools the mkt experts&quot;  {link}           
3    This iPhone #SXSW app would b pretty awesome if it didn't crash every 10mins during extended browsing. #Fuckit #Illmakeitwork                  
4    Line outside the Apple store in Austin waiting for the new iPad #SXSW  {link}                                                                  
Name: tweet, dtype: object

In [187]:
# lowered = df_test['tweet'].apply(lambda x:x.lower())
# tokens = lowered.apply(lambda x:nltk.word_tokenize(x))
# tags = tokens.apply(lambda x:nltk.pos_tag(x))

In [188]:
# from collections import Counter
# counts = tags.apply(lambda x: Counter(tag for word,tag in x))


In [196]:
# pos_cols = pd.DataFrame(dict(counts[0],index=[0])).set_index('index')
# pos_cols

NN  :  WP  NNS  VBP  PRP  VB  .  ,  JJ  FW  #
index                                               
0      8   1  1   2    1    1    1   2  5  3   1   2

In [197]:
# for i in range(1,len(df_test)):
#     pos_cols = pos_cols.append(pd.DataFrame(dict(counts[i],index=[i])).set_index('index'))

In [198]:
# pos_cols.head()

#   $  ''    (    )    ,    .    :   CC  CD ...    VB  VBD  VBG  VBN  \
index                                                ...                        
0      2.0 NaN NaN NaN  NaN   5.0  2.0  1.0 NaN  NaN ...   1.0 NaN  NaN  NaN    
1      7.0 NaN NaN  1.0  1.0 NaN   1.0  2.0  1.0 NaN ...   2.0 NaN  NaN  NaN    
2      2.0 NaN NaN  3.0  3.0 NaN   1.0 NaN   1.0 NaN ...  NaN  NaN   1.0 NaN    
3      1.0 NaN NaN NaN  NaN  NaN  NaN   2.0  1.0 NaN ...  NaN  NaN  NaN  NaN    
4      1.0 NaN NaN NaN  NaN  NaN  NaN  NaN  NaN  NaN ...  NaN   1.0 NaN  NaN    

       VBP  VBZ  WDT   WP  WP$  WRB  
index                                
0      1.0 NaN  NaN   1.0 NaN  NaN   
1     NaN  NaN  NaN  NaN  NaN  NaN   
2     NaN   1.0 NaN  NaN  NaN  NaN   
3     NaN  NaN  NaN  NaN  NaN  NaN   
4     NaN   1.0 NaN  NaN  NaN  NaN   

[5 rows x 43 columns]

In [ ]:
# pos_cols.fillna(0,inplace=True)

In [200]:
# for cols in pos_cols.columns:
#     pos_cols[cols] = pos_cols[cols].astype('int')

In [209]:
# pos_cols = pos_cols.iloc[:,8:][['CC', 'CD', 'DT', 'EX', 'FW', 'IN', 'JJ', 'JJR', 'JJS', 'MD',
#        'NN', 'NNP', 'NNPS', 'NNS', 'PDT', 'POS', 'PRP', 'PRP$', 'RB', 'RBR',
#        'RBS', 'RP', 'SYM', 'TO', 'UH', 'VB', 'VBD', 'VBG', 'VBN', 'VBP', 'VBZ',
#        'WDT', 'WP', 'WRB']]

In [211]:
pos_cols.head()

CC  CD  DT  EX  FW  IN  JJ  JJR  JJS  MD ...   UH  VB  VBD  VBG  VBN  \
index                                           ...                           
0      0   0   0   0   1   0   3   0    0    0  ...   0   1   0    0    0     
1      1   0   0   0   0   1   3   0    1    0  ...   0   2   0    0    0     
2      1   0   1   0   0   1   3   0    0    0  ...   0   0   0    1    0     
3      1   0   1   0   0   4   4   1    0    0  ...   0   0   0    0    0     
4      0   0   0   0   0   1   0   1    0    0  ...   0   0   1    0    0     

       VBP  VBZ  WDT  WP  WRB  
index                          
0      1    0    0    1   0    
1      0    0    0    0   0    
2      0    1    0    0   0    
3      0    0    0    0   0    
4      0    1    0    0   0    

[5 rows x 34 columns]

In [210]:
# pos_cols.iloc[:,8:].to_csv(r'pos_hack_test.csv')

In [10]:
def remove_pattern(input_txt,pattern):
    r = re.findall(pattern, input_txt)
    for match in r:
        input_txt=re.sub(match,'',input_txt)
    return input_txt

In [11]:
df['tweet'] = df['tweet'].apply(lambda row:remove_pattern(str(row), '@[\w]*'))

print(df['tweet'].head())

0    #sxswnui #sxsw #apple defining language of touch with different dialects becoming smaller                                                      
1    Learning ab Google doodles! All doodles should be light, funny &amp; innovative, with exceptions for significant occasions. #GoogleDoodle #sxsw
2    one of the most in-your-face ex. of stealing the show in yrs RT  &quot;At #SXSW, Apple schools the mkt experts&quot;  {link}                   
3    This iPhone #SXSW app would b pretty awesome if it didn't crash every 10mins during extended browsing. #Fuckit #Illmakeitwork                  
4    Line outside the Apple store in Austin waiting for the new iPad #SXSW  {link}                                                                  
Name: tweet, dtype: object


In [12]:
df_test['tweet'] = df_test['tweet'].apply(lambda row:remove_pattern(str(row), '@[\w]*'))

print(df_test['tweet'].head())

0    Audience Q: What prototyping tools do you use? Sketchbooks/sharpie pens, photoshop, Balsamic, Google docs, Axsure, etc. #myprototype #sxsw
1    At SXSW? Send Your Best Photos &amp; Videos to... {link} #citizen_journalism #cnn #ireport #photography #sxsw #Cyber #iPhone              
2      and here's a pic of you winning your ipad! #unsix #sxsw cc    {link} (cont) {link}                                                      
3    Google Marissa Mayer: mobile phone as a cursor of physical location - new version of map fast and more real life like   #sxsw             
4    #SXSW Google maps is even cooler than I thought                                                                                           
Name: tweet, dtype: object


In [13]:
def processTweet(tweet):
    # Remove HTML special entities (e.g. &amp;)
    tweet = re.sub(r'\&\w*;', '', tweet)
    #Convert @username to AT_USER
    tweet = re.sub('@[^\s]+','',tweet)
    # Remove tickers
    tweet = re.sub(r'\$\w*', '', tweet)
    # Remove hyperlinks
    tweet = re.sub(r'https?:\/\/.*\/\w*', '', tweet)
    # Remove hashtags
    tweet = re.sub(r'#\w*', '', tweet)
    # Remove words with 2 or fewer letters
    tweet = re.sub(r'\b\w{1,2}\b', '', tweet)
    # Remove whitespace (including new line characters)
    tweet = re.sub(r'\s\s+', ' ', tweet)
    # Remove single space remaining at the front of the tweet.
    tweet = tweet.lstrip(' ') 
    # Remove characters beyond Basic Multilingual Plane (BMP) of Unicode:
    tweet = ''.join(c for c in tweet if c <= '\uFFFF') 
    # convert emoji into words:
    tweet=emoji.demojize(tweet)
    return tweet


In [14]:
df['tweet'] = df['tweet'].apply(processTweet)

In [15]:
df['tweet'].head()

0    defining language touch with different dialects becoming smaller                                                
1    Learning Google doodles! All doodles should light, funny innovative, with exceptions for significant occasions. 
2    one the most -your-face . stealing the show yrs , Apple schools the mkt experts {link}                          
3    This iPhone app would pretty awesome didn' crash every 10mins during extended browsing.                         
4    Line outside the Apple store Austin waiting for the new iPad {link}                                             
Name: tweet, dtype: object

In [16]:
df_test['tweet'] = df_test['tweet'].apply(processTweet)

In [17]:
df_test['tweet'].head()

0    Audience : What prototyping tools you use? Sketchbooks/sharpie pens, photoshop, Balsamic, Google docs, Axsure, etc. 
1    SXSW? Send Your Best Photos Videos ... {link}                                                                       
2    and here' pic you winning your ipad! {link} (cont) {link}                                                           
3    Google Marissa Mayer: mobile phone cursor physical location - new version map fast and more real life like          
4    Google maps even cooler than thought                                                                                
Name: tweet, dtype: object

In [18]:
# # Remove Punctuation and split 's, 't, 've with a space for filter
# stop_words = list(set(stopwords.words('english')))+list(punctuations)+['÷','``', "'s", "...", "n't",'÷SXSW ','SXSW','{link} ','sxsw','...','“','”','’','…','','','Ä','___,','ü', '___','¡',' _____','«','...']

In [19]:
# df['tweet'] = df['tweet'].apply(lambda row: row.split())
# df['tweet'] = df['tweet'].apply(lambda x:[i for i in x if i not in stop_words])
# df['tweet'] = df['tweet'].apply(lambda x: ' '.join(x))

In [20]:
def text_process(raw_text):
    """
    Takes in a string of text, then performs the following:
    1. Remove all punctuation
    2. Remove all stopwords
    3. Returns a list of the cleaned text
    """
    # Check characters to see if they are in punctuation
    nopunc = [char for char in list(raw_text) if char not in '"#$%&\'()*+,-./:;<=>@[\\]^_`{|}~']

    # Join the characters again to form the string.
    nopunc = ''.join(nopunc)
    
    # Now just remove any stopwords
    return [word for word in nopunc.lower().split() if word.lower() not in stopwords.words('english')]


def remove_words(word_list):
    remove = ['link','sxsw','...','“','”','’','…' ,'÷','``', "'s", "...", "n't",'÷SXSW ','SXSW','{link} ','sxsw','...','“','”','’','…','','','Ä','___,','ü', '___','¡',' _____','«','...']
    return [w for w in word_list if w not in remove]

# -------------------------------------------

# tokenize message column and create a column for tokens
df['tweet'] = df['tweet'].apply(text_process) # tokenize style 1
df['tweet'] = df['tweet'].apply(remove_words) #tokenize style 2
df['tweet'] = df['tweet'].apply(lambda x: ' '.join(x))
df['tweet'].head()

0    defining language touch different dialects becoming smaller                             
1    learning google doodles! doodles light funny innovative exceptions significant occasions
2    one yourface stealing show yrs apple schools mkt experts                                
3    iphone app would pretty awesome crash every 10mins extended browsing                    
4    line outside apple store austin waiting new ipad                                        
Name: tweet, dtype: object

In [21]:
df_test['tweet'] = df_test['tweet'].apply(text_process)
df_test['tweet'] = df_test['tweet'].apply(remove_words)
df_test['tweet'] = df_test['tweet'].apply(lambda x: ' '.join(x))
df_test['tweet'].head()

0    audience prototyping tools use? sketchbookssharpie pens photoshop balsamic google docs axsure etc
1    sxsw? send best photos videos                                                                    
2    pic winning ipad! cont                                                                           
3    google marissa mayer mobile phone cursor physical location new version map fast real life like   
4    google maps even cooler thought                                                                  
Name: tweet, dtype: object

In [22]:
# (r'C:\Users\Anupriya\Documents\GitHub\hack--2\GoogleNews-vectors-negative300.bin\GoogleNews-vectors-negative300.bin',binary=True)

In [23]:
import gensim.models.keyedvectors as wv2
word_vectors = wv2.KeyedVectors.load_word2vec_format(r'C:\Users\jibraan\Downloads\GoogleNews-vectors-negative300.bin',binary=True)
# #model = gensim.models.Word2Vec.load_word2vec_format('./GoogleNews-vectors-negative300.bin.gz', binary=True) import gensim
# import gensim.models.keyedvectors as wv2
# word_vectors = wv2.KeyedVectors.load_word2vec_format(r'C:\Users\Anupriya\Documents\GitHub\hack--2\GoogleNews-vectors-negative300.bin\GoogleNews-vectors-negative300.bin',binary=True)
# #model = gensim.models.Word2Vec.load_word2vec_format('./GoogleNews-vectors-negative300.bin.gz', binary=True)

In [24]:
df['tokens'] = df['tweet'].apply(lambda x:nltk.word_tokenize(x))

In [25]:
final_vecs = []
pass_cnt = 0
fail_cnt = 0
for doc in df.tokens:
    vecs = []
    for word in doc:
        try:
            vecs.append(word_vectors.word_vec(word))
            pass_cnt += 1
        except KeyError as err:
            fail_cnt += 1
        #vecs = np.array([word_vectors.word_vec(word) for word in doc.split()])
    vec_sum = np.array(vecs).mean(axis=0)
    final_vecs.append(vec_sum)
          #total_cnt += 1
          #break

print(len(final_vecs))
print(final_vecs[0].shape)
#word_vectors.word_vec('good')
print(pass_cnt/(pass_cnt+fail_cnt))

7274
(300,)
0.8964520285346155


In [39]:
final_vecs

[array([ 1.73339844e-02, -6.05468750e-02,  1.12792969e-01,  1.04492188e-01,
         1.14746094e-01, -1.41601562e-02,  6.10351562e-02, -2.85156250e-01,
         9.13085938e-02, -5.24902344e-02, -1.14746094e-01, -1.88476562e-01,
         1.30859375e-01,  2.39257812e-01, -2.75878906e-02, -2.99072266e-02,
         1.64062500e-01,  1.10839844e-01, -1.15966797e-02, -2.50000000e-01,
        -1.61132812e-01, -1.91650391e-02, -3.45703125e-01,  1.56250000e-01,
         1.23046875e-01,  1.54296875e-01,  2.80761719e-02,  8.23974609e-03,
         2.63671875e-01,  1.42578125e-01,  4.78515625e-02,  6.98852539e-03,
         2.96875000e-01,  1.46484375e-01, -1.84570312e-01,  3.02734375e-02,
        -1.72851562e-01,  4.19921875e-02,  4.51171875e-01, -2.40478516e-02,
         1.25000000e-01,  1.32812500e-01,  3.22265625e-02, -5.17578125e-02,
        -5.85937500e-02, -8.69140625e-02,  9.39941406e-03,  1.45507812e-01,
         1.70898438e-01, -1.15722656e-01, -5.29785156e-02,  2.64892578e-02,
        -2.5

In [44]:
tfidf_vectorizer = TfidfVectorizer(max_features=1000 , stop_words='english',)

tweets = tfidf_vectorizer.fit_transform(df['tweet']).toarray()
tweets_test = tfidf_vectorizer.transform(df_test['tweet']).toarray()

In [54]:
tweets[0]
#{'sent1':{'word1':val,'word2':val.....}}
wordList = tfidf_vectorizer.get_feature_names()
mainDict = {}
for idx_row,tweet in enumerate(tweets):
    rowDict = {}
    for idx_col,word in enumerate(wordList):
        rowDict[word] = tweets[idx_row][idx_col]
    mainDict[idx_row] = rowDict

In [ ]:
mainDict[0]

In [ ]:
stemmer = PorterStemmer()
df['tweet'] = df['tweet'].apply(lambda x: [stemmer.stem(i) for i in nltk.word_tokenize(x)])
df['tweet'] = df['tweet'].apply(lambda x: ' '.join(x))

In [ ]:
df['tweet'].head()

In [ ]:
stemmer = PorterStemmer()
df_test['tweet'] = df_test['tweet'].apply(lambda x: [stemmer.stem(i) for i in nltk.word_tokenize(x)])
df_test['tweet'] = df_test['tweet'].apply(lambda x: ' '.join(x))

In [ ]:
df_test['tweet'].head()

In [ ]:
tfidf_vectorizer = TfidfVectorizer(max_features=1000 , stop_words='english',)

tweets = tfidf_vectorizer.fit_transform(df['tweet']).toarray()
tweets_test = tfidf_vectorizer.transform(df_test['tweet']).toarray()

In [ ]:
emo_hack = pd.read_csv('emo_hack.csv').iloc[:,1:]
cap_hack = pd.read_csv('cap_hack.csv').iloc[:,1:]
pos_hack = pd.read_csv('pos_hack.csv').iloc[:,1:]
word_count_hack = pd.Series(pd.read_csv('word_count_hack.csv',names=['sd','word_count']).iloc[1:,1:]['word_count'])
polarity_hack = pd.Series(pd.read_csv('polarity_hack.csv',names=['sd','polarity']).iloc[1:,1:]['polarity'])

In [ ]:
emo_hack_test = pd.read_csv('emo_hack_test.csv').iloc[:,1:]
cap_hack_test = pd.read_csv('cap_hack_test.csv').iloc[:,1:]
pos_hack_test = pd.read_csv('pos_hack_test.csv').iloc[:,1:]
word_count_hack_test = pd.Series(pd.read_csv('word_count_hack_test.csv',names=['sd','word_count']).iloc[1:,1:]['word_count'])
polarity_hack_test = pd.Series(pd.read_csv('polarity_hack_test.csv',names=['sd','polarity']).iloc[1:,1:]['polarity'])

In [ ]:
frame1 = pd.concat([emo_hack,cap_hack,pos_hack],axis=1)

In [ ]:
frame_test1 = pd.concat([emo_hack_test,cap_hack_test,pos_hack_test],axis=1)

In [ ]:
frame2 = pd.concat([word_count_hack,polarity_hack],axis=1).reset_index().drop('index',1)

In [ ]:
frame_test2 = pd.concat([word_count_hack_test,polarity_hack_test],axis=1).reset_index().drop('index',1)

In [ ]:
frame1.head(),frame1.shape

In [ ]:
frame2.head(),frame2.shape

In [ ]:
frame_test1.head(),frame_test1.shape

In [ ]:
frame_test2.head(),frame_test2.shape

In [ ]:
data = pd.concat([frame1,frame2,pd.DataFrame(tweets)],axis=1)

In [ ]:
data.head()

In [ ]:
data.shape

In [ ]:
data_test = pd.concat([frame_test1,frame_test2,pd.DataFrame(tweets_test)],axis=1)

In [ ]:
data_test.head()

In [ ]:
data_test.shape

In [ ]:
test_list1 = pd.DataFrame(np.zeros([1819,8]),columns=[':)', ':-(', ':-|', ':-/', ';]', 'xD', ':]', ':O'])

In [ ]:
test_list1.head()

In [ ]:
test_list2 = pd.DataFrame(np.zeros([1819,45]),columns=['HELP ME', 'HELP', 'COOL', 'GREAT', 'GORGEOUS', 'KILLING', 'OOOO', 'LAME', 'I KNEW', 'PLEASE RT', 'REALLY', 'A SHOTGUN', 'SHITE APP','FAIL', 'VERY BAD', 'SCIENTIFIC DICTATORSHIP', 'DELICIOUSLY IRONIC','YAY', 'TOP STORY', 'OOPS', 'AMAZING', 'APPLAUDS', 'AGREED', 'LOST','IMPORTANT', 'VERY IMPORTANT', 'BOOM', 'THE BIG', 'BEAUTIFUL','OH SNAP', 'HOORAY RT', 'APROVEITEM', 'SUCKS', 'DOUCHE CAKE', 'CHAOS','YES PLEASE', 'LIVESTRONG', 'ALL FREE', 'HOOOOOOO', 'THANK YOU','SO COOL', 'TOO MUCH', 'OMG SIGN', 'TOAST', 'I REALLY'])

In [ ]:
test_list2.head()

In [ ]:
test_list3 = pd.DataFrame(np.zeros([1819,10]),columns=['CC', 'CD', 'DT', 'EX', 'FW', 'IN', 'JJ', 'JJR', 'LS', '``'])

In [ ]:
test_list3.head()

In [ ]:
data_test = pd.concat([data_test,test_list1,test_list2,test_list3],axis=1)

In [ ]:
data.columns[:117]

In [ ]:
data.columns[117:]

In [ ]:
data_test = pd.concat([data_test[data.columns[:117]],data_test[data.columns[117:]]],axis=1)

In [ ]:
scaler = MinMaxScaler()
data['polarity'] = scaler.fit_transform(data[['polarity']])

In [ ]:
data_test['polarity'] = scaler.transform(data_test[['polarity']])

In [ ]:
X_train,X_test,y_train,y_test = train_test_split(data,df['sentiment'],test_size=0.3,stratify=df['sentiment'],random_state=15)

In [ ]:
nb = MultinomialNB()
nb.fit(X_train,y_train)
nb_acc = nb.score(X_test,y_test)
nb_pred = nb.predict(X_test)
nb_acc

In [ ]:
print(classification_report(y_test,nb_pred))

In [ ]:
f1_score(y_test,nb_pred,average='weighted')

In [ ]:
nb.score(X_train,y_train)

In [ ]:
model_lr = LogisticRegression(penalty='l2',random_state=42,solver='lbfgs',multi_class='auto',)
model_lr.fit(X_train,y_train)
y_pred_lr = model_lr.predict(X_test)
y_pred_lr_proba = np.array(pd.DataFrame(model_lr.predict_proba(X_test)).iloc[:,1])
model_lr.score(X_test,y_test)

In [ ]:
f1_score(y_test,y_pred_lr,average='weighted')

In [ ]:
print(classification_report(y_test,y_pred_lr))

In [ ]:
sns.countplot(y_train)

In [ ]:
sm = SMOTE(random_state=12,kind = 'svm')
X_train_rs,y_train_rs = sm.fit_resample(X_train,y_train)
# X_train = pd.DataFrame(X_train_rs)
# y_train = pd.Series(y_train_rs)
sns.countplot(y_train_rs)

In [ ]:
model_lr = LogisticRegression(penalty='l2',random_state=42,solver='newton-cg',multi_class='multinomial')
model_lr.fit(X_train_rs,y_train_rs)
y_pred_lr = model_lr.predict(X_test)
y_pred_lr_proba = np.array(pd.DataFrame(model_lr.predict_proba(X_test)).iloc[:,1])
model_lr.score(X_test,y_test)

In [ ]:
f1_score(y_test,y_pred_lr,average='weighted')

In [ ]:
print(classification_report(y_test,y_pred_lr))

In [ ]:
sm = SMOTE(random_state=12,kind = 'svm')
X_rs,y_rs = sm.fit_resample(data,df['sentiment'])
# X_train = pd.DataFrame(X_train_rs)
# y_train = pd.Series(y_train_rs)
sns.countplot(y_rs)

In [77]:
model_lr = LogisticRegression(penalty='l2',random_state=42,solver='newton-cg',multi_class='auto')
model_lr.fit(data,df['sentiment'])
y_valid = model_lr.predict(data_test)
#y_valid_proba = np.array(pd.DataFrame(model_lr.predict_proba(X_test)).iloc[:,1])


In [75]:
print(y_valid.shape)
submission = pd.read_csv('sample_submission.csv')
print(submission['sentiment'].shape)
submission['sentiment'] = y_valid

(1819,)
(1819,)


In [69]:
# submission.to_csv('submission_NLP.csv')

In [308]:
y_valid

array([1, 1, 1, ..., 1, 2, 1], dtype=int64)